
# 地理点构建的图

这个示例展示了如何使用PySAL和geopandas从一组点构建图。在这个示例中，我们将使用1853年约翰·斯诺记录的著名的宽街泵站霍乱病例。这里展示的方法也可以直接使用多边形数据，使用它们的质心作为代表点。


In [ ]:
from libpysal import weights, examples
from contextily import add_basemap
import matplotlib.pyplot as plt
import networkx as nx
import numpy as np
import geopandas

# 从GeoPackage文件中读取示例数据。GeoPackage
# 是一种用于存储地理数据的后备格式
# 通过sqlite。geopandas 读取数据依赖于 fiona 包，
# 提供一个高层次的、类似pandas风格的地理数据接口。
cases = geopandas.read_file("cholera_cases.gpkg")

# 构建质心的坐标数组
coordinates = np.column_stack((cases.geometry.x, cases.geometry.y))

# 构建两种不同类型的图：

## 3-近邻图，意味着点之间相互连接
## 到其他三个最近的点。这意味着每个点
## 将恰好有三个邻居。
knn3 = weights.KNN.from_dataframe(cases, k=3)

## 50米距离带图将连接所有点对
## 彼此之间距离在50米以内的点。这意味着这些点
## 可能具有不同数量的邻居。
dist = weights.DistanceBand.from_array(coordinates, threshold=50)

# 然后，我们可以使用该方法将图转换为networkx对象
# .to_networkx() method.
knn_graph = knn3.to_networkx()
dist_graph = dist.to_networkx()

# 要使用networkx进行绘图，我们需要将节点重新合并
# 为了在networkx中绘制，调整它们的位置
positions = dict(zip(knn_graph.nodes, coordinates))

# plot with a nice basemap
f, ax = plt.subplots(1, 2, figsize=(8, 4))
for i, facet in enumerate(ax):
    cases.plot(marker=".", color="orangered", ax=facet)
    try:  # 关于在CI中下载/解析底图的问题
        add_basemap(facet)
    except:
        pass
    facet.set_title(("KNN-3", "50-meter Distance Band")[i])
    facet.axis("off")
nx.draw(knn_graph, positions, ax=ax[0], node_size=5, node_color="b")
nx.draw(dist_graph, positions, ax=ax[1], node_size=5, node_color="b")
plt.show()